# Classification with LSTM

****Sandya Subramanian****

****HST (Health Sciences and Technology), 2nd year Ph.D.****

### Setup ###

In [1]:
using CSV, Plots, Images
using Knet, AutoGrad
using Knet: sigm_dot, tanh_dot
using StatsBase

In [2]:
Knet.gpu(0)

0

In [3]:
include("findpeaks.jl")
include("pan_tompkins.jl")
include("run_pan_tompkins.jl")
include("get_breaks.jl")
include("get_dataset.jl")
include("get_comb_dataset.jl")
include("get_traintest.jl")

get_traintest (generic function with 1 method)

## LSTM ## 

After seeing that classification was really successful with just MLP, I decided to try LSTM just to see if it made a difference to have the time dependencies already encoded. Since ECG is a very regular signal in time, one would expect that temporal dependencies really matter.

In [21]:
#Task 1: Create dictionary
function createVocabulary(mode)
    vocab = Dict{Int64,Int64}()
    # Depends on if binary or multiclass
    if mode == "binary"
        for i = 1:2
            vocab[i] = i
        end
    else
        for i = 1:8
            vocab[i] = i
        end
    end
    return vocab
end

#LSTM Network Function
function lstm(weight,bias,hidden,cell,input)
    gates   = hcat(input,hidden) * weight .+ bias
    hsize   = size(hidden,2) #size of layer
    forget  = sigm_dot(gates[:,1:hsize]) #Assumed size H+I * 4H
    ingate  = sigm_dot(gates[:,1+hsize:2hsize])
    outgate = sigm_dot(gates[:,1+2hsize:3hsize])
    change  = tanh_dot(gates[:,1+3hsize:end])
    cell    = cell .* forget + ingate .* change
    hidden  = outgate .* tanh_dot(cell)
    return (hidden,cell)
end

#Task 2: Create Initial Weights
function initweights(lenhidden, lenvocab, embed, arraytype)
    init(d...) = xavier(d...)
    bias(d...) = zeros(d...)
    tmp_model = Vector{Array{Float32}}(2*length(lenhidden)+2) #2*num layers + 2
    X = embed #size of x input (721)
    for k = 1:length(lenhidden)
        tmp_model[2k-1] = init(X+lenhidden[k],4*lenhidden[k]) #Each element of the Vector is a matrix itself
        tmp_model[2k] = bias(1,4*lenhidden[k])
        #Combine all the weights
        #Biases separately
        X = lenhidden[k] #Replace previous layer size
    end
    #INPUT
    #tmp_model[end-2] = init(lenvocab,embed) #Size of vocab by size of input x?
    #OUTPUT - ok as is
    tmp_model[end-1] = init(lenhidden[end],lenvocab) #Size of last layer by number of words - for output?
    tmp_model[end] = bias(1,lenvocab) #Zero vector for each word?
    
    if arraytype == "KnetArray"
        model = Vector{KnetArray{Float32}}(2*length(lenhidden)+2)
        for k = 1:length(tmp_model)
            model[k] = KnetArray{Float32}(tmp_model[k]);
        end
    else
        model = copy(tmp_model);
    end
    return model
end

#Task 3: Create Initial State
function initstate(model, batch)
    #Check what type to use
    if typeof(model[1]) == Array{Float64,2}
        arraytype = "Array"
    else 
        arraytype = "KnetArray"
    end
    nlayers = div(length(model)-2,2)
    state = Vector{Any}(2*nlayers)
    for k = 1:nlayers
        #Get length of layer
        H = div(size(model[2k],2),4)
        state[2k-1] = state[2k] = zeros(batch,H)
        #cell and hidden for each layer both vectors length H
    end
    
    if arraytype == "KnetArray"
        for k = 1:length(state)
            state[k] = KnetArray{Float32}(state[k]);
        end
    end
    return state
end

#Task 4: Create Predict function
function predict(model, state, input; pdrop=0)
    input = KnetArray(input');
    nlayers = div(length(model)-2,2)
    newstate = similar(state)
    for k = 1:nlayers
        #Run through by selecting the right elements corresponding to that layer
        #state[2k-1] -> hidden
        #state[2k] -> cell
        #model[2k-1] -> weights
        #model[2k] -> bias
        hidden, cell = lstm(model[2k-1],model[2k],state[2k-1],state[2k],input)
        newstate[2k-1] = hidden
        newstate[2k] = cell
        input = hidden
    end
    output = input * model[end-1] .+ model[end] #To get outputs
    return output,newstate
end

function accuracy_LSTM(model,state,data,p; average=true)
    sum = cnt = 0
    for (x,y) in data
        sum += accuracy(p(model,state,x)[1]',y)
        cnt += 1
    end
    average ? sum / cnt : sum
end

#Task 5: Create Loss Function
function loss(model, state, x_batch, y; newstate=nothing, pdrop=0)
    preds,newstate = predict(model,state,x_batch)
    if newstate != nothing
        copy!(newstate, map(AutoGrad.getval,state))
    end
    return nll(preds',y)
end

#Task 6: Create Train Function
function train(model, dtrn, optim, lossgradient, options; pdrop=0)
    state = initstate(model, options["batchsize"])
    for (x,y) in dtrn
        #temp = model[1]
        grads = lossgradient(model, state, x, y; newstate=state, pdrop=pdrop)
        update!(model, grads, optim)
        #println(sum(model[1]-temp))
    end
    return model
end

train (generic function with 1 method)

In [7]:
function prep_dataset(subj_list,fs)
    abn_dataset, full_dataset, abn_truth_cats, full_bin_cats, label_key = get_comb_dataset(subj_list,fs)
    println(countmap(abn_truth_cats))
    println(countmap(full_bin_cats))
    xtst_mc, ytst_mc, xtrn_mc, ytrn_mc, xtst_bin, ytst_bin, xtrn_bin, ytrn_bin = get_traintest(abn_dataset,full_dataset,abn_truth_cats,full_bin_cats,0.1)
    
    return xtst_mc, ytst_mc, xtrn_mc, ytrn_mc, xtst_bin, ytst_bin, xtrn_bin, ytrn_bin 
end

prep_dataset (generic function with 1 method)

In [8]:
function setup(numepochs,lenhidden,mode,arraytype)
  #Options
  lenhidden    = lenhidden;          # Sizes of one or more LSTM layers.

  options1 = Dict{String,Any}()
  options1["togenerate"]   = Int64(4000)            # If non-zero generate given number of characters.
  options1["epochs"]       = Int64(numepochs)      # Number of epochs for training.
  options1["embed"]        = Int64(721)            # Size of the embedding vector.
  options1["batchsize"]    = Int64(50)            # Number of sequences to train on in parallel
 # options1["seqlength"]    = Int64(721)             # Maximum number of steps to unroll the network for bptt. Initial epochs will use the epoch number as bptt length for faster convergence.
  options1["seed"]         = -1            # Random number seed. -1 or 0 is no fixed seed
  options1["lr"]           = 0.001           # Initial learning rate
  options1["gclip"]        = 3.0           # Value to clip the gradient norm at.
  options1["dpout"]        = 0.0            # Dropout probability.  

  #options1["seed"] > 0 && srand(options1["seed"])

  # Prep dataset
  #xtst_mc, ytst_mc, xtrn_mc, ytrn_mc, xtst_bin, ytst_bin, xtrn_bin, ytrn_bin = prep_dataset([207,212,203,209,201],360)
  xtst_mc, ytst_mc, xtrn_mc, ytrn_mc, xtst_bin, ytst_bin, xtrn_bin, ytrn_bin = prep_dataset([207, 212, 203, 209, 201, 202, 205, 208, 210, 213, 220, 221, 222, 230, 111, 112, 113, 114, 115, 116, 117, 118, 119, 121, 122, 123, 124, 100, 101, 103, 104, 106, 108, 109, 232, 233, 234],360)
  signal = [xtst_mc, ytst_mc, xtrn_mc, ytrn_mc, xtst_bin, ytst_bin, xtrn_bin, ytrn_bin]

  vocab = createVocabulary(mode);
  info("$(length(vocab)) unique values.") # The output should be 75 unique chars for input.txt

  #Now, let's compute the accuracy of a random model
  model = initweights(lenhidden, length(vocab), options1["embed"], arraytype);
    
  return options1, lenhidden, signal, vocab, model
end

function getbatches(options1,signal,mode)
  #Now we are ready. First, let's see the intial loss.
  #Feed input matrix based on mode
  if mode == "binary"
    dtrn =  minibatch(signal[7], signal[8], options1["batchsize"]);
    dtst =  minibatch(signal[5], signal[6], options1["batchsize"]);
  else
    dtrn =  minibatch(signal[3], signal[4], options1["batchsize"]);
    dtst =  minibatch(signal[1], signal[2], options1["batchsize"]);
  end
  return dtrn,dtst
end

function setuptrain(options1, dtrn, dtst, model)
  # Knet magic
  lossgradient = grad(loss,1);

  # Print the loss of train and test sets with random model.
  firststate = initstate(model, options1["batchsize"])
  println((:epoch,0,:train,accuracy_LSTM(model,firststate,dtrn,predict),:test,accuracy_LSTM(model,firststate,dtst,predict)))

  #Below is the training part of RNN (with Adam)
  optim = map(x->Adam(lr=options1["lr"], gclip=options1["gclip"]), model);
  return lossgradient, optim
end

function trainloop(options1, vocab, dtrn, dtst, lossgradient, optim, model)
  # MAIN LOOP
  firststate = initstate(model, options1["batchsize"])
  for epoch=1:options1["epochs"]
      @time train(model, dtrn, optim, lossgradient, options1; pdrop=options1["dpout"])
      # Calculate and print the losses after each epoch
      println((:epoch,epoch,:train,accuracy_LSTM(model,firststate,dtrn,predict),:test,accuracy_LSTM(model,firststate,dtst,predict)))  
    end
  return model
end

trainloop (generic function with 1 method)

In [9]:
function main(numepochs,lenhidden,mode,arraytype)
    options1, lenhidden, signal, vocab, model = setup(numepochs,lenhidden,mode,arraytype)
    dtrn,dtst = getbatches(options1, signal, mode)
    lossgradient, optim = setuptrain(options1, dtrn, dtst, model)
    model = trainloop(options1, vocab, dtrn, dtst, lossgradient, optim, model)
end

main (generic function with 1 method)

**Binary Classification**

Interestingly enough, I was able to achieve the same high accuracy but with far fewer layers. Perhaps the inherent structure of the LSTM simplifies the number of layers necessary.

In [16]:
main(100,[128],"binary","KnetArray")

Dict(7=>4332,4=>1380,2=>3096,3=>3730,5=>4332,8=>1404,6=>1770,1=>4348)
Dict(2=>24392,1=>19264)


INFO: 2 unique values.


(:epoch, 0, :train, 0.5580891719745236, :test, 0.5645977011494253)
  1.179427 seconds (1.05 M allocations: 256.373 MiB, 3.07% gc time)
(:epoch, 1, :train, 0.895694267515923, :test, 0.8979310344827585)
  1.120322 seconds (1.06 M allocations: 256.546 MiB, 3.44% gc time)
(:epoch, 2, :train, 0.9309554140127395, :test, 0.9289655172413791)
  1.122957 seconds (1.06 M allocations: 256.517 MiB, 3.42% gc time)
(:epoch, 3, :train, 0.9430573248407673, :test, 0.9402298850574707)
  1.122412 seconds (1.06 M allocations: 256.489 MiB, 3.42% gc time)
(:epoch, 4, :train, 0.9470573248407692, :test, 0.945057471264367)
  1.121317 seconds (1.05 M allocations: 256.426 MiB, 3.16% gc time)
(:epoch, 5, :train, 0.9539872611465025, :test, 0.9514942528735626)
  1.117789 seconds (1.06 M allocations: 256.538 MiB, 3.48% gc time)
(:epoch, 6, :train, 0.9576305732484135, :test, 0.9554022988505741)
  1.118980 seconds (1.06 M allocations: 256.509 MiB, 3.43% gc time)
(:epoch, 7, :train, 0.9600254777070121, :test, 0.95655172

  1.119681 seconds (1.05 M allocations: 256.422 MiB, 3.16% gc time)
(:epoch, 61, :train, 0.982624203821662, :test, 0.9698850574712643)
  1.235869 seconds (1.06 M allocations: 256.533 MiB, 12.93% gc time)
(:epoch, 62, :train, 0.9848917197452277, :test, 0.9721839080459769)
  1.109420 seconds (1.06 M allocations: 256.505 MiB, 3.46% gc time)
(:epoch, 63, :train, 0.9840254777070113, :test, 0.9724137931034482)
  1.104185 seconds (1.06 M allocations: 256.442 MiB, 3.23% gc time)
(:epoch, 64, :train, 0.9824968152866294, :test, 0.9682758620689654)
  1.109334 seconds (1.06 M allocations: 256.554 MiB, 3.48% gc time)
(:epoch, 65, :train, 0.9842292993630618, :test, 0.9712643678160918)
  1.232618 seconds (1.06 M allocations: 256.526 MiB, 12.97% gc time)
(:epoch, 66, :train, 0.9828280254777122, :test, 0.9698850574712643)
  1.104491 seconds (1.06 M allocations: 256.496 MiB, 3.45% gc time)
(:epoch, 67, :train, 0.9853757961783484, :test, 0.9717241379310341)
  1.106468 seconds (1.06 M allocations: 256.435

4-element Array{Knet.KnetArray{Float32,N} where N,1}:
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010218200000, 1738752, 0, nothing), (849, 512))
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x000001024ec0e800, 2048, 0, nothing), (1, 512))     
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010207060000, 1024, 0, nothing), (128, 2))     
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x00000102070bb800, 8, 0, nothing), (1, 2))          

**Multi-class classification**

Here I needed 3 layers, but still achieved the same high accuracy as with MLP. Perhaps the time dependencies between different types of arrhyhtmias are less straightforward, which makes sense.

In [17]:
main(100,[128,256,64],"multiclass","KnetArray")

Dict(7=>4332,4=>1380,2=>3096,3=>3730,5=>4332,8=>1404,6=>1770,1=>4348)
Dict(2=>24392,1=>19264)


INFO: 8 unique values.


(:epoch, 0, :train, 0.16756264236902055, :test, 0.16458333333333333)
  1.284043 seconds (1.35 M allocations: 172.399 MiB, 2.45% gc time)
(:epoch, 1, :train, 0.7764009111617307, :test, 0.7870833333333334)
  1.238067 seconds (1.36 M allocations: 172.573 MiB, 2.57% gc time)
(:epoch, 2, :train, 0.8395899772209562, :test, 0.8391666666666667)
  1.238087 seconds (1.35 M allocations: 172.485 MiB, 2.50% gc time)
(:epoch, 3, :train, 0.8577676537585408, :test, 0.8541666666666666)
  1.238547 seconds (1.36 M allocations: 172.557 MiB, 2.56% gc time)
(:epoch, 4, :train, 0.8883826879271054, :test, 0.8774999999999998)
  1.229925 seconds (1.34 M allocations: 172.362 MiB, 2.30% gc time)
(:epoch, 5, :train, 0.9061958997722074, :test, 0.8995833333333332)
  1.229643 seconds (1.35 M allocations: 172.528 MiB, 2.59% gc time)
(:epoch, 6, :train, 0.9079726651480616, :test, 0.9004166666666666)
  1.229925 seconds (1.36 M allocations: 172.607 MiB, 2.62% gc time)
(:epoch, 7, :train, 0.9131662870159434, :test, 0.9041

(:epoch, 61, :train, 0.9734851936218673, :test, 0.9545833333333333)
  1.226200 seconds (1.34 M allocations: 172.360 MiB, 2.30% gc time)
(:epoch, 62, :train, 0.9907061503416862, :test, 0.9820833333333332)
  1.233775 seconds (1.35 M allocations: 172.526 MiB, 2.57% gc time)
(:epoch, 63, :train, 0.9889749430523925, :test, 0.9741666666666666)
  1.233276 seconds (1.36 M allocations: 172.606 MiB, 2.61% gc time)
(:epoch, 64, :train, 0.9892027334851944, :test, 0.9779166666666667)
  1.232770 seconds (1.35 M allocations: 172.499 MiB, 2.56% gc time)
(:epoch, 65, :train, 0.9866970387243739, :test, 0.9724999999999998)
  1.232299 seconds (1.36 M allocations: 172.576 MiB, 2.65% gc time)
(:epoch, 66, :train, 0.9911161731207295, :test, 0.9783333333333334)
  1.232592 seconds (1.35 M allocations: 172.380 MiB, 2.33% gc time)
(:epoch, 67, :train, 0.9912528473804111, :test, 0.977083333333333)
  1.263242 seconds (1.36 M allocations: 172.546 MiB, 2.63% gc time)
(:epoch, 68, :train, 0.9955808656036453, :test, 0

8-element Array{Knet.KnetArray{Float32,N} where N,1}:
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010243200000, 1738752, 0, nothing), (849, 512)) 
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010206e33800, 2048, 0, nothing), (1, 512))      
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010274e00000, 1572864, 0, nothing), (384, 1024))
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x000001024ed75800, 4096, 0, nothing), (1, 1024))     
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010256580000, 327680, 0, nothing), (320, 256))  
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x00000102071a0c00, 1024, 0, nothing), (1, 256))      
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x0000010206f91000, 2048, 0, nothing), (64, 8))       
 Knet.KnetArray{Float32,2}(Knet.KnetPtr(Ptr{Void} @0x000001020715c800, 32, 0, nothing), (1, 8))          